In [ ]:
# For Google Colab
# Install folium package.
!pip install folium

In [ ]:
# For Google Colab
# Mount your Google drive and copy all files from "AI_HW2" directory
# in your Google drive to current directory.
from google.colab import drive
drive.mount('/content/gdrive')
!cp -r ./gdrive/MyDrive/AI_HW2/* .

In [1]:
# Don't change this part.
# For load graph information and show map
import folium
import pickle
def load_path_graph(path):
    with open('graph.pkl', 'rb') as f:
        graph = pickle.load(f)

    node_pairs = list(zip(path[:-1], path[1:]))
    lines = []
    for edge in graph:
        if (edge['u'], edge['v']) in node_pairs or  (edge['v'], edge['u']) in node_pairs:
            lines.append(edge['geometry'])
    return lines

In [2]:
# Part 1~4 and 6
# You can write your code in this file directly.
# Or you can wirte in new .py files and import it.
# ex: from astar import astar

In [3]:
# import module
import csv
from collections import deque
import heapq

# read csv
with open('edges.csv', newline='') as f:
    reader = csv.reader(f)
    edges = list(reader)

with open('heuristic.csv', newline='') as f:
    reader = csv.reader(f)
    heuristic = list(reader)

In [4]:
# Part 1
# version 1.0
def bfs(start, end):
    """
    Parameters:
        start: Integer. The starting node ID.
        end: Integer. The end node ID.
    Returns:
        path: List of integer. The path you found, stored as a list of node IDs. The first is starting node ID.
              The last is end node ID.
        dist: : Float. The distance of the path you found. (Unit:meter)
        num_visited: Integer. The number of nodes were visited when you search.
    """
    queue = deque()
    queue.append(start)
    id_path = {start: [start]}
    id_distance = {start: 0.0}
    num_visited_nodes = 0
    is_reach_end = False
    while True:
        current_node_idx = queue.popleft()
        next_nodes = []
        for row in edges: 
            if row[0] == str(current_node_idx):
                next_nodes.append(row)
        next_nodes_idx = [int(row[1]) for row in next_nodes]
        next_nodes_distance = [float(row[2]) for row in next_nodes]
        for row_idx in range(len(next_nodes)):
            next_node_idx = next_nodes_idx[row_idx]
            if id_distance.get(next_node_idx) == None:
                if next_node_idx == end:
                    is_reach_end = True
                num_visited_nodes += 1
                queue.append(next_node_idx)
                id_distance[next_node_idx] = id_distance[current_node_idx] + next_nodes_distance[row_idx]
                id_path[next_node_idx] = list(id_path[current_node_idx])
                id_path[next_node_idx].append(next_node_idx)
                if is_reach_end:
                    break
        if is_reach_end or len(queue) == 0:
            break
    if is_reach_end:
        path = id_path[end]
        dist = id_distance[end]
    else:
        path = -1
        dist = -1
        print(f'The path from {start} to {end} with BFS doesn\'t exist!')
    num_visited = num_visited_nodes
    return path, dist, num_visited

# version 2.0
# def bfs(start, end):
#     """
#     Parameters:
#         start: Integer. The starting node ID.
#         end: Integer. The end node ID.
#     Returns:
#         path: List of integer. The path you found, stored as a list of node IDs. The first is starting node ID.
#               The last is end node ID.
#         dist: : Float. The distance of the path you found. (Unit:meter)
#         num_visited: Integer. The number of nodes were visited when you search.
#     """
#     n_idx = len(set(edges['end']))
#     distance = [[0] * n_idx for _ in range(n_idx)]
#     visited_idx = []
#     visited_idx.append(start)
#     precede = []
#     precede.append(0)
#     queue = deque()
#     queue.append(start)
#     is_reach_end = False
#     num_visited_nodes = 0
#     while True:
#         current_node_idx = queue.popleft()
#         next_nodes = []
#         for row in edges: 
#             if row[0] == str(current_node_idx):
#                 next_nodes.append(row)
#         next_nodes_idx = [int(row[1]) for row in next_nodes]
#         next_nodes_distance = [float(row[2]) for row in next_nodes]
#         for row_idx in range(len(next_nodes)):
#             next_node_idx = next_nodes_idx[row_idx]
#             if next_node_idx not in visited_idx:
#                 visited_idx.append(next_node_idx)
#                 if distance[visited_idx.index(current_node_idx), visited_idx.index(next_node_idx)] == -1:
#                     num_visited_nodes += 1
#                     precede.append(idx.index(current_node_idx))
#                     distance[visited_idx.index(current_node_idx)][visited_idx.index(next_node_idx)] = next_nodes_distance[row_idx]
#                     distance[visited_idx.index(next_node_idx)][visited_idx.index(current_node_idx)] = next_nodes_distance[row_idx]
#                     queue.append(next_node_idx)
#             if next_node_idx == end:
#                 is_reach_end = True
#         if is_reach_end or len(queue) == 0:
#             break
#     if is_reach_end:
#         path = [len(visited_idx) - 1]
#         dist = 0
#         while True:
#             now_idx = path[-1]
#             precede_idx = precede[now_idx]
#             dist += distance[precede_idx][now_idx]
#             path.append(precede_idx)
#             if precede_idx == 0:
#                 break
#         path.reverse()
#         for i in range(len(path)):
#             path[i] = visited_idx[path[i]]
#     else:
#         path = -1
#         dist = -1
#         print(f'The path from {start} to {end} with BFS doesn\'t exist!')
#     num_visited = num_visited_nodes
#     return path, dist, num_visited

In [5]:
# Part 2
# version 1.0
def dfs(start, end):
    """
    Parameters:
        start: Integer. The starting node ID.
        end: Integer. The end node ID.
    Returns:
        path: List of integer. The path you found, stored as a list of node IDs. The first is starting node ID.
              The last is end node ID.
        dist: : Float. The distance of the path you found. (Unit:meter)
        num_visited: Integer. The number of nodes were visited when you search.
    """
    end_points = [row[1] for row in edges]
    n_idx = len(set(end_points))
    distance = [[0] * n_idx for _ in range(n_idx)]
    visited_idx = []
    visited_idx.append(start)
    precede = []
    precede.append(0)
    stack = deque()
    stack.append(start)
    is_reach_end = False
    num_visited_nodes = 0
    is_should_pop = True
    while True:
        current_node_idx = stack[-1]
        next_nodes = []
        for row in edges: 
            if row[0] == str(current_node_idx):
                next_nodes.append(row)
        next_nodes_idx = [int(row[1]) for row in next_nodes]
        next_nodes_distance = [float(row[2]) for row in next_nodes]
        is_should_pop = True
        for row_idx in range(len(next_nodes) - 1, -1, -1):
            next_node_idx = next_nodes_idx[row_idx]
            if next_node_idx not in visited_idx:
                if next_node_idx == end:
                    is_reach_end = True
                visited_idx.append(next_node_idx)
                precede.append(visited_idx.index(current_node_idx))
                num_visited_nodes += 1
                distance[visited_idx.index(current_node_idx)][visited_idx.index(next_node_idx)] = next_nodes_distance[row_idx]
                distance[visited_idx.index(next_node_idx)][visited_idx.index(current_node_idx)] = next_nodes_distance[row_idx]
                stack.append(next_node_idx)
                is_should_pop = False
                break
        if is_should_pop:
            current_node_idx = stack.pop()
        if is_reach_end or len(stack) == 0:
            break

    if is_reach_end:
        path = [len(visited_idx) - 1]
        dist = 0
        while True:
            now_idx = path[-1]
            precede_idx = precede[now_idx]
            dist += distance[precede_idx][now_idx]
            path.append(precede_idx)
            if precede_idx == 0:
                break
        path.reverse()
        for i in range(len(path)):
            path[i] = visited_idx[path[i]]
    else:
        path = -1
        dist = -1
        print(f'The path from {start} to {end} with DFS doesn\'t exist!')
    num_visited = num_visited_nodes
    return path, dist, num_visited


# version 2.0
# def dfs(start, end):
#     """
#     Parameters:
#         start: Integer. The starting node ID.
#         end: Integer. The end node ID.
#     Returns:
#         path: List of integer. The path you found, stored as a list of node IDs. The first is starting node ID.
#               The last is end node ID.
#         dist: : Float. The distance of the path you found. (Unit:meter)
#         num_visited: Integer. The number of nodes were visited when you search.
#     """
#     stack = deque()
#     stack.append(start)
#     id_path = {start: [start]}
#     id_distance = {start: 0.0}
#     num_visited_nodes = 0
#     is_reach_end = False
#     while True:
#         current_node_idx = stack.pop()
#         next_nodes = edgesnext_nodes = []
#         for row in edges: 
#             if row[0] == str(current_node_idx):
#                 next_nodes.append(row)
#         next_nodes_idx = [int(row[1]) for row in next_nodes]
#         next_nodes_distance = [float(row[2]) for row in next_nodes]
#         for row_idx in range(len(next_nodes)):(len(next_nodes.index)):
#             next_node_idx = next_nodes_idx[row_idx]
#             if id_distance.get(next_node_idx) == None:
#                 if next_node_idx == end:
#                     is_reach_end = True
#                 num_visited_nodes += 1
#                 stack.append(next_node_idx)
#                 id_distance[next_node_idx] = id_distance[current_node_idx] + next_nodes_distance[row_idx]
#                 id_path[next_node_idx] = list(id_path[current_node_idx])
#                 id_path[next_node_idx].append(next_node_idx)
#                 if is_reach_end:
#                     break
#         if is_reach_end or len(stack) == 0:
#             break
#     if is_reach_end:
#         path = id_path[end]
#         dist = id_distance[end]
#     else:
#         path = -1
#         dist = -1
#         print(f'The path from {start} to {end} with DFS doesn\'t exist!')
#     num_visited = num_visited_nodes
#     return path, dist, num_visited

In [6]:
# Part 3
def ucs(start, end):
    """
    Parameters:
        start: Integer. The starting node ID.
        end: Integer. The end node ID.
    Returns:
        path: List of integer. The path you found, stored as a list of node IDs. The first is starting node ID.
              The last is end node ID.
        dist: : Float. The distance of the path you found. (Unit:meter)
        num_visited: Integer. The number of nodes were visited when you search.
    """
    end_points = [row[1] for row in edges]
    n_idx = len(set(end_points))
    distance = [[0] * n_idx for _ in range(n_idx)]
    visited_idx = []
    visited_idx.append(start)
    precede = []
    precede.append(0)
    is_reach_end = False
    num_visited_nodes = 0
    heap = [(0, start)]
    accumulated_distance = [0]
    while True:
        current_node_idx = heapq.heappop(heap)[-1]
        next_nodes = []
        for row in edges: 
            if row[0] == str(current_node_idx):
                next_nodes.append(row)
        next_nodes_idx = [int(row[1]) for row in next_nodes]
        next_nodes_distance = [float(row[2]) for row in next_nodes]
        next_nodes_accumulated_distance = []
        if current_node_idx in visited_idx:
            for row_idx in range(len(next_nodes_idx)): 
                next_node_accumulated_distance = next_nodes_distance[row_idx] + accumulated_distance[visited_idx.index(current_node_idx)]
                next_nodes_accumulated_distance.append(next_node_accumulated_distance)
        node_tuples = list(zip(next_nodes_accumulated_distance, next_nodes_idx))
        for node_tuple in node_tuples:
            if node_tuple[-1] not in visited_idx: 
                heapq.heappush(heap, node_tuple)
        for next_node_tuple in heap:
            next_node_accumulated_distance, next_node_idx = next_node_tuple
            if next_node_idx not in visited_idx:
                visited_idx.append(next_node_idx)
                num_visited_nodes += 1
                precede.append(visited_idx.index(current_node_idx))
                accumulated_distance.append(next_node_accumulated_distance)
                distance[visited_idx.index(current_node_idx)][visited_idx.index(next_node_idx)] = next_node_accumulated_distance - accumulated_distance[precede[visited_idx.index(next_node_idx)]]
                distance[visited_idx.index(next_node_idx)][visited_idx.index(current_node_idx)] = next_node_accumulated_distance - accumulated_distance[precede[visited_idx.index(next_node_idx)]]
            if next_node_idx == end:
                is_reach_end = True
        if is_reach_end or len(heap) == 0:
            break
    if is_reach_end:
        path = [len(visited_idx) - 1]
        dist = 0
        while True:
            now_idx = path[-1]
            precede_idx = precede[now_idx]
            dist += distance[precede_idx][now_idx]
            path.append(precede_idx)
            if precede_idx == 0:
                break
        path.reverse()
        for i in range(len(path)):
            path[i] = visited_idx[path[i]]
    else:
        path = -1
        dist = -1
        print(f'The path from {start} to {end} with UCS doesn\'t exist!')
    num_visited = num_visited_nodes
    return path, dist, num_visited

In [7]:
# Part 4
def astar(start, end):
    """
    Parameters:
        start: Integer. The starting node ID.
        end: Integer. The end node ID.
    Returns:
        path: List of integer. The path you found, stored as a list of node IDs. The first is starting node ID.
              The last is end node ID.
        dist: : Float. The distance of the path you found. (Unit:meter)
        num_visited: Integer. The number of nodes were visited when you search.
    """
    end_points = [row[1] for row in edges]
    n_idx = len(set(end_points))
    distance = [[0] * n_idx for _ in range(n_idx)]
    visited_idx = []
    visited_idx.append(start)
    precede = []
    precede.append(0)
    is_reach_end = False
    num_visited_nodes = 0
    heap = [(0, start, 99999)]
    accumulated_distance = [0]
    while True:
        current_node_idx = heapq.heappop(heap)[1]
        next_nodes = []
        for row in edges: 
            if row[0] == str(current_node_idx):
                next_nodes.append(row)
        next_nodes_idx = [int(row[1]) for row in next_nodes]
        next_nodes_distance = [float(row[2]) for row in next_nodes]
        heuristic_distance = []
        nodes_total_distance = []
        heuristic_distance_list = []
        if current_node_idx in visited_idx:
            for row_idx in range(len(next_nodes_idx)):
                next_nodes_accumulated_distance = next_nodes_distance[row_idx] + accumulated_distance[visited_idx.index(current_node_idx)]
                heuristic_distance = 0
                for row in heuristic:
                    if row[0] == str(next_nodes_idx[row_idx]):
                        end_idx = -1
                        for end_id in heuristic[0]:
                            if end_id == str(end):
                                break
                            end_idx += 1
                        heuristic_distance = float(row[1 + end_idx])
                heuristic_distance_list.append(heuristic_distance)
                nodes_total_distance.append(next_nodes_accumulated_distance + heuristic_distance)
        node_tuples = list(zip(nodes_total_distance, next_nodes_idx, heuristic_distance_list))
        for node_tuple in node_tuples:
            if node_tuple[1] not in visited_idx: 
                heapq.heappush(heap, node_tuple)
        for next_node_tuple in heap:
            node_total_distance, next_node_idx, heuristic_distance = next_node_tuple
            next_node_accumulated_distance = node_total_distance - heuristic_distance
            if next_node_idx not in visited_idx:
                visited_idx.append(next_node_idx)
                num_visited_nodes += 1
                precede.append(visited_idx.index(current_node_idx))
                accumulated_distance.append(next_node_accumulated_distance)
                distance[visited_idx.index(current_node_idx)][visited_idx.index(next_node_idx)] = next_node_accumulated_distance - accumulated_distance[precede[visited_idx.index(next_node_idx)]]
                distance[visited_idx.index(next_node_idx)][visited_idx.index(current_node_idx)] = next_node_accumulated_distance - accumulated_distance[precede[visited_idx.index(next_node_idx)]]
            if next_node_idx == end:
                is_reach_end = True
        if is_reach_end or len(heap) == 0:
            break
    if is_reach_end:
        path = [len(visited_idx) - 1]
        dist = 0
        while True:
            now_idx = path[-1]
            precede_idx = precede[now_idx]
            dist += distance[precede_idx][now_idx]
            path.append(precede_idx)
            if precede_idx == 0:
                break
        path.reverse()
        for i in range(len(path)):
            path[i] = visited_idx[path[i]]
    else:
        path = -1
        dist = -1
        print(f'The path from {start} to {end} with ASTAR doesn\'t exist!')
    num_visited = num_visited_nodes
    return path, dist, num_visited

In [8]:
# Part 5
# Change start ID and end ID.
start = 1718165260
end = 8513026827

In [9]:
# Don't change this part.
# Show the result of BFS
bfs_path, bfs_dist, bfs_visited = bfs(start, end)
print(f'The number of nodes in the path found by BFS: {len(bfs_path)}')
print(f'Total distance of path found by BFS: {bfs_dist} m')
print(f'The number of visited nodes in BFS: {bfs_visited}\n')

fmap = folium.Map(location=(24.806383132251874, 120.97685775516189), zoom_start=13)
for line in load_path_graph(bfs_path):
    fmap.add_child(folium.PolyLine(locations=line, tooltip='bfs', weight=4, color='blue'))
fmap

The number of nodes in the path found by BFS: 183
Total distance of path found by BFS: 15442.395000000002 m
The number of visited nodes in BFS: 11241



In [10]:
# Don't change this part.
# Show the result of DFS
dfs_path, dfs_dist, dfs_visited = dfs(start, end)
print(f'The number of nodes in the path found by DFS: {len(dfs_path)}')
print(f'Total distance of path found by DFS: {dfs_dist} m')
print(f'The number of visited nodes in DFS: {dfs_visited}\n')

fmap = folium.Map(location=(24.806383132251874, 120.97685775516189), zoom_start=13)
for line in load_path_graph(dfs_path):
    fmap.add_child(folium.PolyLine(locations=line, tooltip='dfs', weight=4, color='green'))
fmap

The number of nodes in the path found by DFS: 1521
Total distance of path found by DFS: 64821.60399999999 m
The number of visited nodes in DFS: 3291



In [11]:
# Don't change this part.
# Show the result of UCS
ucs_path, ucs_dist, ucs_visited = ucs(start, end)
print(f'The number of nodes in the path found by UCS: {len(ucs_path)}')
print(f'Total distance of path found by UCS: {ucs_dist} m')
print(f'The number of visited nodes in UCS: {ucs_visited}\n')

fmap = folium.Map(location=(24.806383132251874, 120.97685775516189), zoom_start=13)
for line in load_path_graph(ucs_path):
    fmap.add_child(folium.PolyLine(locations=line, tooltip='ucs', weight=4, color='violet'))
fmap

The number of nodes in the path found by UCS: 275
Total distance of path found by UCS: 14241.51 m
The number of visited nodes in UCS: 11929



In [12]:
# Don't change this part.
# Show the result of A* search
astar_path, astar_dist, astar_visited = astar(start, end)
print(f'The number of nodes in the path found by A* search: {len(astar_path)}')
print(f'Total distance of path found by A* search: {astar_dist} m')
print(f'The number of visited nodes in A* search: {astar_visited}\n')

fmap = folium.Map(location=(24.806383132251874, 120.97685775516189), zoom_start=13)
for line in load_path_graph(astar_path):
    fmap.add_child(folium.PolyLine(locations=line, tooltip='astar', weight=4, color='red'))
fmap

The number of nodes in the path found by A* search: 277
Total distance of path found by A* search: 14218.25499999999 m
The number of visited nodes in A* search: 7089



In [13]:
# Part 6 (Bonus)
# admissible heuristic function is heuristic_distance / speed_limit
def astar_time(start, end):
    """
    Parameters:
        start: Integer. The starting node ID.
        end: Integer. The end node ID.
    Returns:
        path: List of integer. The path you found, stored as a list of node IDs. The first is starting node ID.
              The last is end node ID.
        dist: : Float. The distance of the path you found. (Unit:meter)
        num_visited: Integer. The number of nodes were visited when you search.
    """
    end_points = [row[1] for row in edges]
    n_idx = len(set(end_points))
    time = [[0] * n_idx for _ in range(n_idx)]
    visited_idx = []
    visited_idx.append(start)
    precede = []
    precede.append(0)
    is_reach_end = False
    num_visited_nodes = 0
    # dist, index, heuristic, speed limit
    heap = [(0, start, 999999, 1)]
    accumulated_time = [0]
    while True:
        current_node_idx = heapq.heappop(heap)[1]
        next_nodes = []
        for row in edges: 
            if row[0] == str(current_node_idx):
                next_nodes.append(row)
        next_nodes_idx = [int(row[1]) for row in next_nodes]
        next_nodes_distance = [float(row[2]) for row in next_nodes]
        next_nodes_speed_limit = [float(row[-1]) for row in next_nodes]
        next_nodes_time = []
        nodes_total_accumulated_time = []
        heuristic_distance_list = []
        if current_node_idx in visited_idx:
            for row_idx in range(len(next_nodes_idx)):
                next_node_speed_limit = next_nodes_speed_limit[row_idx] * 1000 / 3600
                next_node_time = next_nodes_distance[row_idx] / next_node_speed_limit
                next_nodes_time.append(next_node_time)
                next_nodes_accumulated_time = next_node_time + accumulated_time[visited_idx.index(current_node_idx)]
                heuristic_distance = 0
                for row in heuristic:
                    if row[0] == str(next_nodes_idx[row_idx]):
                        end_idx = -1
                        for end_id in heuristic[0]:
                            if end_id == str(end):
                                break
                            end_idx += 1
                        heuristic_distance = float(row[1 + end_idx])
                heuristic_distance_list.append(heuristic_distance)
                heuristic_time = heuristic_distance / next_node_speed_limit
                nodes_total_accumulated_time.append(next_nodes_accumulated_time + heuristic_time)
        node_tuples = list(zip(nodes_total_accumulated_time, next_nodes_idx, heuristic_distance_list, next_nodes_speed_limit))
        for node_tuple in node_tuples:
            if node_tuple[1] not in visited_idx: 
                heapq.heappush(heap, node_tuple)
        for next_node_tuple in heap:
            next_node_total_accumulated_time, next_node_idx, heuristic_distance, next_node_speed_limit = next_node_tuple
            next_node_speed_limit = next_node_speed_limit * 1000 / 3600
            heuristic_time = heuristic_distance / next_node_speed_limit
            next_node_accumulated_time = next_node_total_accumulated_time - heuristic_time
            if next_node_idx not in visited_idx:
                visited_idx.append(next_node_idx)
                num_visited_nodes += 1
                precede.append(visited_idx.index(current_node_idx))
                accumulated_time.append(next_node_accumulated_time)
                time[visited_idx.index(current_node_idx)][visited_idx.index(next_node_idx)] = next_node_accumulated_time - accumulated_time[precede[visited_idx.index(next_node_idx)]]
                time[visited_idx.index(next_node_idx)][visited_idx.index(current_node_idx)] = next_node_accumulated_time - accumulated_time[precede[visited_idx.index(next_node_idx)]]
            if next_node_idx == end:
                is_reach_end = True
        if is_reach_end or len(heap) == 0:
            break
    if is_reach_end:
        path = [len(visited_idx) - 1]
        dist = 0
        while True:
            now_idx = path[-1]
            precede_idx = precede[now_idx]
            dist += time[precede_idx][now_idx]
            path.append(precede_idx)
            if precede_idx == 0:
                break
        path.reverse()
        for i in range(len(path)):
            path[i] = visited_idx[path[i]]
    else:
        path = -1
        dist = -1
        print(f'The path from {start} to {end} with ASTAR doesn\'t exist!')
    num_visited = num_visited_nodes
    return path, dist, num_visited

In [14]:
# Part 6 (Bonus)
# Don't change this part.
# Show the shortest time result of A* search
time_path, time, time_visited = astar_time(start, end)
print(f'The number of nodes in the path found by A* search: {len(time_path)}')
print(f'Total second of path found by A* search: {time} s')
print(f'The number of visited nodes in A* search: {time_visited}\n')

fmap = folium.Map(location=(24.806383132251874, 120.97685775516189), zoom_start=13)
for line in load_path_graph(time_path):
    fmap.add_child(folium.PolyLine(locations=line, tooltip='astar', weight=4, color='red'))
fmap

The number of nodes in the path found by A* search: 233
Total second of path found by A* search: 915.3859068561263 s
The number of visited nodes in A* search: 5996



In [ ]:
# For Google Colab
# Remember to execute this line once you've modified any .py file
# Save the .py code you have modified to your Google Drive
!cp ./*.py ./gdrive/MyDrive/AI_HW2/